In [2]:
import numpy as np
import polars as pl
from pathlib import Path

import matplotlib.pyplot as plt
plt.rcParams["font.size"] = 16

# 2.A : Few trajectories + Mean + Theory (Homogeneous)

In [29]:
# --- Load files --- #
root = Path("//home/nicolas/Documents/Workspace/nucleo/outputs/2026-02-24__PC/nucleo__fig_0")
paths = [str(p) for p in root.glob("*/**/*.parquet")] or [str(p) for p in root.glob("*/*.parquet")]
df_all = (
    pl.scan_parquet(paths)
    .collect()
    .sort(by=[
        "algorithm", "fact", "factmode",
        "landscape", "s", "l", "lmbda", "alphar"
        ])
)
thetas = np.unique(df_all["theta"].to_numpy())


# --- Figure --- #
for idx, theta_val in enumerate(thetas[0:2]):

    # --- Data ---
    df_theta = df_all.filter(pl.col("theta") == theta_val)
    trajs = df_theta["results"][0].to_numpy()
    mean_traj = df_theta["results_mean"][0].to_numpy()
    v_mean_th = df_theta["v_mean_th"].to_numpy()
    times = df_theta["times"][0].to_numpy()
    mu = df_theta["mu"].to_numpy()

    # --- Figure ---
    plt.figure(figsize=(10,6), dpi=1200)

    # Trajectoires individuelles
    plt.plot(trajs[0], drawstyle="steps-post",
             color="red", alpha=0.30, label="trajectories")
    for i in range(1, 10):
        plt.plot(trajs[i], drawstyle="steps-post",
                 color="red", alpha=0.30)

    # Moyenne simulée
    plt.plot(mean_traj,
             color="red", ls="-", lw=2,
             label=r"$v_{mean}$")

    # Vitesse homogène théorique
    plt.scatter(times, times*v_mean_th,
                color="black", lw=2,
                label=r"$v_{homogeneous}$",
                marker="+")

    # Mise en forme
    plt.ylim([-100, 2100])
    plt.grid(True, alpha=0.3)
    plt.title(f"(μ,θ) = ({mu[0]},{theta_val})")
    plt.xlabel("time")
    plt.ylabel("position")
    plt.legend()

    plt.tight_layout()
    plt.show()

# 2.B : Their distributions of speeds

In [30]:
import matplotlib.pyplot as plt
import matplotlib.cm as cm
from matplotlib.lines import Line2D
plt.rcParams["font.size"] = 16

plt.figure(figsize=(10,6), dpi=1200)

def th_instantaneous_speeds(mu, theta, v, alpha0=10/160, k0=1):
    a = (mu / theta) ** 2
    b = mu / (theta ** 2)
    return (alpha0 * k0) * (a*b) * (v*b)**(a-1) / (alpha0*k0 + b*v)**(a+1)


cmap = cm.get_cmap("viridis")
n_colors = len(thetas[0:2])
color_list = [cmap(0.0 + 0.50*i/(n_colors-1)) for i in range(n_colors)]
color_list.reverse()

for idx, theta_val in enumerate(thetas[0:2]):

    df_theta = df_all.filter(pl.col("theta") == theta_val)
    vi_points = df_theta["vi_points"][0].to_numpy()
    vi_distrib = df_theta["vi_distrib"][0].to_numpy()
    v_mean = df_theta["v_mean"].to_numpy()

    # Simulation (avec label couleur)
    plt.plot(
        vi_points,
        vi_distrib,
        color=color_list[idx],
        ls="-",
        lw=2,
        alpha=0.70,
        label=f"(μ,θ)=({mu[0]},{theta_val})"
    )

    # Théorie (sans label)
    plt.plot(
        vi_points,
        th_instantaneous_speeds(mu, theta_val, vi_points),
        color=color_list[idx],
        ls="--",
        lw=2,
        alpha=0.70,
        label="_nolegend_"
    )

    # v_mean (sans label)
    plt.axvline(
        x=v_mean,
        color=color_list[idx],
        ls=":",
        lw=2,
        alpha=0.70,
        label="_nolegend_"
    )


# =========================
#        LÉGENDES
# =========================

ax = plt.gca()

# Légende couleurs (μ,θ)
leg1 = ax.legend(loc="upper right")
ax.add_artist(leg1)

# Légende styles
style_legend = [
    Line2D([0], [0], color="black", lw=2, ls="-", label="Simulation"),
    Line2D([0], [0], color="black", lw=2, ls="--", label="Theory"),
    Line2D([0], [0], color="black", lw=2, ls=":", label=r"$v_{mean}/2$")
]

ax.legend(handles=style_legend, loc="upper left")


plt.xlabel(r'speeds in ($\sigma k_0$) unit')
plt.ylabel("Distribution")
plt.xlim([1e-1, 1e4])
plt.ylim([1e-7, 1e1])
plt.xscale("log")
plt.yscale("log")
plt.grid(True, alpha=0.3, which="both")

plt.show()

/tmp/ipykernel_28562/2221516080.py:14: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  cmap = cm.get_cmap("viridis")
/tmp/ipykernel_28562/2221516080.py:11: RuntimeWarning: overflow encountered in power
  return (alpha0 * k0) * (a*b) * (v*b)**(a-1) / (alpha0*k0 + b*v)**(a+1)
/tmp/ipykernel_28562/2221516080.py:11: RuntimeWarning: overflow encountered in multiply
  return (alpha0 * k0) * (a*b) * (v*b)**(a-1) / (alpha0*k0 + b*v)**(a+1)
/tmp/ipykernel_28562/2221516080.py:11: RuntimeWarning: invalid value encountered in divide
  return (alpha0 * k0) * (a*b) * (v*b)**(a-1) / (alpha0*k0 + b*v)**(a+1)
